In [9]:
#First we import the libraries we will need
import urllib
import urllib2
#import urllib.request
import time
from bs4 import BeautifulSoup
import re
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

In [10]:
#First of all we need to find all the name of the sites that belong to fortune 500. This can happen if we seperate
#The information needed from the below link
url = "http://www.zyxware.com/articles/4344/list-of-fortune-500-companies-and-their-websites"
list_company_number =[]
list_company_name = []
list_company_website = []
list500_sites = []
list500_names = []
list500_num = []
list500_url = []

In [11]:
#In order to extract the needed informations we will create 3 lists. The first one will contain the rank of each site, the
#second one will contain the name of the company and the 3rd one will contain the actual link of the company's site.
#For achieving this purpose we will create a funstion that will in its turn create those three list.
#In order to know if the function worked we will ask it to return the first element of each list along with a sentence.
def websites (url):
    #browser = urllib.request.build_opener()
    browser = urllib2.build_opener() #because i work from different computers with different pyhton version some commands are not recognizable in each version
    browser.addheaders = [('User-agent', 'Mozilla/5.0')]
    response = browser.open(url)# this might throw an exception if something goes wrong.
    myHTML = response.read()
    soup = BeautifulSoup(myHTML,"lxml")    
    o = 0
    td_list =[]
    for row2 in soup.html.body.findAll('td'):
        td_list.insert(o, row2)
        o = o + 1
    a = 0
    b = 1
    c = 2
    list_numbering = 0
    for i in range (0,500):        
        num = str(td_list[a])
        company = str(td_list[b])
        site = str(td_list[c])
        c_num = re.findall('>(.+?)</td>',num)  
        c_num = str(c_num[0])
        c_name = re.findall('>(.+?)</td>',company)
        c_name = str(c_name[0])
        c_site = re.findall('">(.+?)</a>',site)
        c_site = str(c_site[0])        
        list_company_number.insert(list_numbering,c_num)
        list_company_name.insert(list_numbering,c_name)
        list_company_website.insert(list_numbering,c_site)
        a = a + 3
        b = b + 3
        c = c + 3
        list_numbering =  list_numbering + 1 
    print ('The three lists are ready')
    print (list_company_number[0])
    print (list_company_name[0])
    print (list_company_website[0])

In [12]:
# After creating the function we should now test that it actually works correctly
websites (url)

The three lists are ready
1
Walmart
www.walmart.com


In [15]:
## The next step is to download and save in a new list the 500 sites.
## We will create a new function that will do this by reading the list "list_company_websites" that we created 
## with the previous function

def list_company_HTML (list_company_website,list_company_name,start,end):
    import time
    #browser2 = urllib.request.build_opener()
    browser2 = urllib2.build_opener()
    browser2.addheaders = [('User-agent', 'Mozilla/5.0')]
    for i in range (start,end):
        k = str(i+1)
        lc = str(list_company_website[i])        
        lc = lc.replace("'","")   
        lc = lc.replace("[","")
        lc = lc.replace("]","")
        lcn = str(list_company_name[i])        
        lcn = lcn.replace("'","")   
        lcn = lcn.replace("[","")
        lcn = lcn.replace("]","")
        url2= 'http://'+lc
        #an exception might be thrown, so the code should be in a try-except block
        try:
            #use the browser to get the url.
            response2=browser2.open(url2)# this might throw an exception if something goes wrong.
        except Exception: # this describes what to do if an exception is thrown
             continue#ignore this page.      
        #read the response in html format. This is essentially a long piece of text
        myHTML2=response2.read()
        list500_sites.insert(i,myHTML2)
        list500_names.insert(i,lcn)
        list500_url.insert(i,lc)
        list500_num.insert(i,k)
        #wait for 2 seconds
        time.sleep(2)
        #print ("The site " + k + " has been downloaded!")
    print ("We downloaded: ",len(list500_sites)," sites!")
    #print (len(list500_names),list500_names)

In [16]:
start = 0
stop = 25
for i in range (0,1): #i am not downloading all the pages for the time being for reasons of running faster the process during the tests
    print (start)
    print (stop)    
    list_company_HTML (list_company_website,list_company_name,start,stop)
    start = stop
    stop = stop + 25

0
25
('We downloaded: ', 24, ' sites!')


In [17]:
#As we can see there is one site that hasn't been downloaded in order to keep track of the sites that we could not download
#we will create a new list that we will keep them all together there
not_d = []
def not_downloadables (list500_names,list_company_name):
    met = 0
    for i in range(0,25):#normally it would be till 500 but now we test for the first 25 we have downloaded
        ct = list_company_name[i]
        if ct not in list500_names:
            not_d.insert(met,ct)
    print(not_d)        

In [18]:
#Now we will run the function to see which sites haven;t been downloaded
not_downloadables (list500_names,list_company_name)

['Fannie Mae']


In [19]:
#Retreiving the social media from each site
#First create empty lists for the ones that we will need to calculate
sm_f = []
sm_t = []
sm_i = []
sm_p = []
sm_y = []
sm_l = []   
sm_nm = [] 
nm = []
sm_url = []

In [20]:
#Then create a function that will feel in those lists so as to make the data frame later on

def socialmedia (list500_sites,list500_names,list500_url):
    for num in range(len(list500_names)):
        if list500_sites[num] != "":
            hand = str(list500_sites[num])
            sm = ['facebook.com','twitter.com','instagram.com','pinterest.com','youtube.com','linkedin.com'] 
            number = 0 
            for index in range(len(sm)):
                x = sm[index]
                photo = re.findall(x,hand)                                
                if (len(photo)>0):
                    if x == 'facebook.com':
                        answerf = 'yes'
                    if x == 'twitter.com':
                        answert = 'yes'
                    if x == 'instagram.com':
                        answeri = 'yes'
                    if x == 'pinterest.com':
                        answerp = 'yes'
                    if x == 'youtube.com':
                        answery = 'yes'
                    if x =='linkedin.com':
                        answerl = 'yes'                   
                else:
                     if x == 'facebook.com':
                        answerf = 'no'
                     if x == 'twitter.com':
                        answert = 'no'
                     if x == 'instagram.com':
                        answeri = 'no'
                     if x == 'pinterest.com':
                        answerp = 'no'
                     if x == 'youtube.com':
                        answery = 'no'
                     if x =='linkedin.com':
                        answerl = 'no'                 
            sm_nm.insert(num,list500_names[num]) 
            nm.insert(num,num)
            sm_url.insert(num,list500_url[num])
            sm_f.insert(num,answerf)
            sm_t.insert(num,answert)
            sm_i.insert(num,answeri)
            sm_p.insert(num,answerp)
            sm_y.insert(num,answery)
            sm_l.insert(num,answerl)

In [21]:
#Now we will run the function for the 25 first sites for starters
socialmedia (list500_sites,list500_names,list500_url)

In [22]:
#Finally we create the data frame with the elements we found            
d = {'company' : pd.Series(sm_nm, index=[nm]),'url' : pd.Series(sm_url, index=[nm]),
     'facebook' : pd.Series(sm_f, index=[nm]),'twitter' : pd.Series(sm_t, index=[nm]),
     'instagram' : pd.Series(sm_i, index=[nm]),'pinterest' : pd.Series(sm_p, index=[nm]),
     'youtube' : pd.Series(sm_y, index=[nm]),'linkedin' : pd.Series(sm_l, index=[nm]),}
social_media = pd.DataFrame(d)    
social_media.head(3) #we see the first 3 in the data frame

company facebook instagram linkedin pinterest twitter  \
0      Walmart      yes       yes       no       yes     yes   
1  Exxon Mobil       no        no       no        no      no   
2        Apple       no        no      yes        no      no   

                  url youtube  
0     www.walmart.com     yes  
1  www.exxonmobil.com      no  
2       www.apple.com     yes

In [23]:
#Create the lists we will need for the data frame
l_nm = []
l_ex = []
l_in = []
l_t = []
nm = []
l_url = []

In [24]:
#create the function that will calculate the different type of links
def links (list500_sites,list500_names,list500_url):
    for num in range(len(list500_names)):
        line = str(list500_sites[num])
        href = re.findall('href',line)
        external = re.findall('href="https:',line)
        ex = (len(external))
        alllinks = (len(href))
        internal =  (len(href) - len(external))
        l_nm.insert(num,list500_names[num])            
        l_ex.insert(num,ex)
        l_t.insert(num,alllinks)
        l_in.insert(num,internal)
        nm.insert(num,num)
        l_url.insert(num,list500_url[num])

In [25]:
#Run the function in order to find the external, internal and total links of each site
#For now we are running for the first 25 sites only
links (list500_sites,list500_names,list500_url)

In [26]:
#Create a dataframe so as to be able to see the results of the function we run
d2 = {'company' : pd.Series(l_nm, index=[nm]),'url' : pd.Series(l_url, index=[nm]),
      'external' : pd.Series(l_ex, index=[nm]),'internal' : pd.Series(l_in, index=[nm]),
     'total links' : pd.Series(l_t, index=[nm])}
sites_links = pd.DataFrame(d2)    
sites_links.head(3) #we see the first 3 in the data frame

company  external  internal  total links                 url
0      Walmart        68        97          165     www.walmart.com
1  Exxon Mobil        23       783          806  www.exxonmobil.com
2        Apple         5       277          282       www.apple.com

In [27]:
#The initial lists we will need in order to calculate the loading time
lt_nm = [] 
lt_time = []
nm = []
lt_url = []

In [28]:
#the function that will calculate the loading time
def loadtime (list_company_website,list500_names,list500_url):
    from time import time
    #browser2 = urllib.request.build_opener()
    browser2 = urllib2.build_opener()
    browser2.addheaders = [('User-agent', 'Mozilla/5.0')]
    for num in range(len(list500_names)):
        lc = str(list_company_website[num])        
        lc = lc.replace("'","")   
        lc = lc.replace("[","")
        lc = lc.replace("]","")
        url2= 'http://'+lc        
        try:
            response2=browser2.open(url2)
        except Exception: 
             continue#     
        start_time = time()
        myHTML2=response2.read()
        end_time = time()
        response2.close()
        l_t = round(end_time-start_time, 3) #in order to be more redable we rounded the time
        loadt = str(l_t)
        lt_nm.insert(num,list500_names[num])            
        lt_time.insert(num,loadt)
        nm.insert(num,num)
        lt_url.insert(num,list500_url[num])

In [29]:
#running the function for the first 25 sites
loadtime (list_company_website,list500_names,list500_url)

In [30]:
#creating the data frame with the loading times
d3 = {'company' : pd.Series(lt_nm, index=[nm]),'url' : pd.Series(lt_url, index=[nm]),
      'loading time' : pd.Series(lt_time, index=[nm])}
loading_time = pd.DataFrame(d3)    
loading_time.head(3) #we see the first 3 in the data frame

company loading time                 url
0      Walmart        0.385     www.walmart.com
1  Exxon Mobil        3.881  www.exxonmobil.com
2        Apple        0.094       www.apple.com

In [31]:
#Find out how many and what type of images each site has
#first we create the initially empty lists
p_p = []
p_d = []
p_jpg = []
p_jpeg = []
p_gif = []
p_tif = []
p_tiff = []
p_bmp = []
p_jpe = []
p_nm = []
p_tt =[]
nm = []
p_url = []

In [32]:
#Then we create the function that will explore the html pages and search for the images
def images (list500_sites,list500_names,list500_url):
    for num in range(len(list500_names)):
        line = str(list500_sites[num])
        image = ['.png','.dib','.jpg','.jpeg','.bmp','.jpe','.gif','.tif','.tiff'] 
        totalnumber = 0 
        for index in range(len(image)):
            x = image[index]
            photo = re.findall(x,line)
            if x == '.png':
                p = str (len(photo))
            if x == '.dib':
                d = str (len(photo))
            if x == '.jpg':
                jpg = str (len(photo))
            if x == '.jpeg':
                jpeg = str (len(photo))
            if x == '.gif':
                gif = str (len(photo))
            if x == '.tif':
                tif = str (len(photo))
            if x == '.tiff':
                tiff = str (len(photo))
            if x == '.bmp':
                bmp = str (len(photo))
            if x == '.jpe':
                jpe = str (len(photo))
            totalnumber = len(photo) + totalnumber
        total = str (totalnumber)
        p_nm.insert(num,list500_names[num])            
        p_p.insert(num,p)  
        p_d.insert(num,d)  
        p_jpg.insert(num,jpg)  
        p_jpeg.insert(num,jpeg)  
        p_gif.insert(num,gif)  
        p_tif.insert(num,tif)  
        p_tiff.insert(num,tiff)  
        p_bmp.insert(num,bmp)  
        p_jpe.insert(num,jpe)  
        p_tt.insert(num,total)
        nm.insert(num,num)
        p_url.insert(num,list500_url[num])

In [33]:
#Then we run the function for the first 20 sites for now
images (list500_sites,list500_names,list500_url)

In [34]:
#Finally we create a dataframe in order to see the results of the function
d4 = {'company' : pd.Series(p_nm, index=[nm]),'url' : pd.Series(p_url, index=[nm]),
      '.png' : pd.Series(p_p, index=[nm]),'.dib' : pd.Series(p_d, index=[nm]),
'.jpg' : pd.Series(p_jpg, index=[nm]),'.jpeg' : pd.Series(p_jpeg, index=[nm]),
'.bmp' : pd.Series(p_bmp, index=[nm]),'.jpe' : pd.Series(p_jpe, index=[nm]),
'.gif' : pd.Series(p_gif, index=[nm]),'.tif' : pd.Series(p_tif, index=[nm]),
'.tiff' : pd.Series(p_tiff, index=[nm]), 'total images' : pd.Series(p_tt, index=[nm])}
images_types = pd.DataFrame(d4)    
images_types.head(3) #we see the first 3 in the data frame

.bmp .dib .gif .jpe .jpeg .jpg .png .tif .tiff      company total images  \
0    0    0   22  103   103   76   43    6     0      Walmart          353   
1    0    0    1    0     0   16    2    4     0  Exxon Mobil           23   
2    0    0    1    0     0    0    2    0     0        Apple            3   

                  url  
0     www.walmart.com  
1  www.exxonmobil.com  
2       www.apple.com

In [35]:
#Now we will find the different dimensions that each site uses
#initially we create the empty lists we will need
nm = []
s_comp = []
s_dimensions = []
s_times = []
s_tt_dif_dim = []
ht = [] #list of different heights in each case
wt = [] #list of different widths in each case
h_w = [] # combinations of height and width
dif_size = []  
un_size = [] 
s_url = []

In [36]:
#With the below function we will gather in a variable all the different dimensions 
#and in another one all the times that each dimension occures for each html code
def find_dif_sizes (list500_sites,list500_names,list500_url):
    for num in range(len(list500_names)):
        nm.insert(num,num)                  
        s_comp.insert(num,list500_names[num])
        s_url.insert(num,list500_url[num])
        line = str(list500_sites[num]) #read each line of the list500_sites that contains each html code
        soup = BeautifulSoup(line, "lxml")
        # we create 2 local variables so as to gather the different dimensions and occurencies  of each page seperately
        s_dimensions_local = []
        s_times_local = []
        hw = 0 # we use it for the lists of height and width
        for tag in soup.find_all('img'): # find all the img in the first site html
            #Since in some cases either the height or the width is missing we would like to keep only the ones that have both dimensions
             h = tag.attrs.get('height', None)
             w = tag.attrs.get('width', None)
             #we use if to check which ones have both        
             if h != None:
                 if w != None:
                     ht.insert(hw,h)
                     wt.insert(hw,w)
                     hw = hw+1                        
        hw2 = 0
        for l in range(len(ht)):
             h_w_c = ht[l] + 'x' + wt[l]    #we create a str with the form (300x300) so as to be more easily to read later on 
             h_w.insert(hw2,h_w_c)  #we put it in a new list
             hw2 = hw2 + 1    
        if h_w == []:#we check if there are not any dimensions available
             nm.insert(num,num)                  
             s_comp.insert(num,list500_names[num])
             s_dimensions.insert(num,0)
             s_times.insert(num,0)    
        if h_w != []:#now we continue with the cases where the dimensions are indeed available             
             from collections import Counter
             hw_unique = Counter(h_w)
             hw_unique2 = str(hw_unique) #the unique different dimensions for the specific site
            #Due to the fact that we are talking about a list we have to split the parts we need 
             split1 = hw_unique2.split('{')
             a=split1[1]
             split2 =a.split('}')
             b=split2[0]
             split3 = b.split(',')
             finalsplit=[]
             fs = []
             z=0
             m=1
             j = 0
             z1=0
             m1=1
            #each of the items in split3 has a form '300x300 : 15' and in order to create the dataframe we have 
            #to split this form and keep the informations in different list
             for numb in split3:                
                 oldstring = numb
                 newstring = oldstring.replace("'", "")
                 new = newstring.replace("'","")
                 string = new.replace(" ","")
                 finalstring = string.split(':')
                    #the finalstring is a list that contains the dimensions and the occurencies
                    #in order toseperate in different lists we create an additional loop
                 for xx in range(len(finalstring)):
                     ax = finalstring[xx]
                     if 'x' in ax:
                         s_dimensions_local.insert(z1,finalstring[xx])
                         z1 = z1 +1
                     else:
                         s_times_local.insert(m1,finalstring[xx])
                         m1 = m1 +1  
            #Now we can add to the lists the parts we created so as to have them all gathered together             
             s_dimensions.insert(num,s_dimensions_local)
             s_times.insert(num,s_times_local)                
    print("Completed")
    print (s_comp,nm)

In [37]:
#Run the function for the first 20 sites
find_dif_sizes (list500_sites,list500_names,list500_url)

Completed
(['Walmart', 'Exxon Mobil', 'Apple', 'Berkshire Hathaway', 'McKesson', 'UnitedHealth Group', 'CVS Health', 'General Motors', 'Ford Motor', 'AT&amp;T', 'General Electric', 'AmerisourceBergen', 'Verizon', 'Chevron', 'Costco', 'Kroger', 'Amazon.com', 'Walgreens Boots Alliance', 'HP', 'Cardinal Health', 'Express Scripts Holding', 'J.P. Morgan Chase', 'Boeing', 'Microsoft'], [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23])


In [38]:
#Find the unique different image dimensions and put them on a list
def unique_dif_sizes (s_dimensions,list500_names):
    ds=0
    for num in range(len(list500_names)):
        for s in s_dimensions[num]:
            dif_size.insert(ds,s)
            ds=ds+1
    dsu = 0
    for i in dif_size:
        if i not in un_size:
            un_size.insert(dsu,i)
            dsu = dsu + 1
    print(un_size)        

In [39]:
#Run the finction unique_dif_sizes
unique_dif_sizes (s_dimensions,list500_names)

['144x144', '15x75', '44x556', '800x1200', '24pxx133px', '21pxx173px', '70x125', '1x1', '50x45', '400x300', '292pxx292px', '200pxx200px', '1279pxx984px', '300pxx1500px', '29x29']


In [40]:
#The lists we will need for the next function
t_f_s = []
ttf = []

In [41]:
#Function in order to check whether or not each company has these dimensions
def dimensions_per_company (un_size,list500_names):
    t_f_s.insert(0,un_size)
    ttf.insert(0,t_f_s)
    for num in range(len(list500_names)):
        s1a = s_dimensions[num] #dimensions of site num
        where =[] #empty list
        wh=0
        haveornot = []
        for er in range (len(un_size)):
            for sizea in s1a:
                if sizea == un_size[er]:
                    where.insert(wh,str(er))
                    break
            if str(er) in where:
               haveornot.insert(er,True)                    
            else:
               haveornot.insert(er,False)
                    
        t_f_s.insert(num+1,haveornot)
        ttf.insert(num+1,t_f_s)  

In [42]:
#Run the function dimensions_per_company
dimensions_per_company (un_size,list500_names)

In [43]:
print(s_comp)

['Walmart', 'Exxon Mobil', 'Apple', 'Berkshire Hathaway', 'McKesson', 'UnitedHealth Group', 'CVS Health', 'General Motors', 'Ford Motor', 'AT&amp;T', 'General Electric', 'AmerisourceBergen', 'Verizon', 'Chevron', 'Costco', 'Kroger', 'Amazon.com', 'Walgreens Boots Alliance', 'HP', 'Cardinal Health', 'Express Scripts Holding', 'J.P. Morgan Chase', 'Boeing', 'Microsoft']


In [44]:
#Create an initial dataframe where we will add the sizes later on
d7 = {'company' : pd.Series(s_comp, index=[nm]),'url' : pd.Series(s_url, index=[nm])}
sizess = pd.DataFrame(d7)    
sizess.head(3)

company                 url
0      Walmart     www.walmart.com
1  Exxon Mobil  www.exxonmobil.com
2        Apple       www.apple.com

In [45]:
#Now we want to break the variable t_f_s in order to add the columns to the dataframe                  
#Finally we create the data frame with the elements we found 
def final_dimensions_dataframe (un_size,t_f_s,list500_names):
    for q in range(len(un_size)):
        names = un_size[q]
        var = []
        for num in range(len(list500_names)):
            a = t_f_s[num+1]
            var.insert(num,a[q])
        sizess[names] = pd.Series(var, index=sizess.index)    

In [46]:
#Run the function final_dimensions_dataframe
final_dimensions_dataframe (un_size,t_f_s,list500_names)
sizess.head(3)

company                 url 144x144  15x75 44x556 800x1200 24pxx133px  \
0      Walmart     www.walmart.com    True  False  False    False      False   
1  Exxon Mobil  www.exxonmobil.com    True  False  False    False      False   
2        Apple       www.apple.com    True  False  False    False      False   

  21pxx173px 70x125    1x1  50x45 400x300 292pxx292px 200pxx200px  \
0      False  False  False  False   False       False       False   
1      False  False  False  False   False       False       False   
2      False  False  False  False   False       False       False   

  1279pxx984px 300pxx1500px  29x29  
0        False        False  False  
1        False        False  False  
2        False        False  False

In [51]:
#Now we would like to find the words in the text and the unique words of each html page
#First of all we need to have a dictionary with which we would check if the word we found truly exists
#The dictionary is available in the internet from a github acount from where we are going to read it
url_dictionary = "https://raw.githubusercontent.com/dwyl/english-words/master/words.txt"
#browser = urllib.request.build_opener()
browser = urllib2.build_opener()
browser.addheaders = [('User-agent', 'Mozilla/5.0')]
response = browser.open(url_dictionary)
html_dictionary = response.read()
html_dictionary
dicti = str(html_dictionary)
dicti

'&c\n\'d\n\'em\n\'ll\n\'m\n\'mid\n\'midst\n\'mongst\n\'prentice\n\'re\n\'s\n\'sblood\n\'sbodikins\n\'sdeath\n\'sfoot\n\'sheart\n\'shun\n\'slid\n\'slife\n\'slight\n\'snails\n\'strewth\n\'t\n\'til\n\'tis\n\'twas\n\'tween\n\'twere\n\'twill\n\'twixt\n\'twould\n\'un\n\'ve\n1080\n10th\n1st\n2\n2nd\n3rd\n4th\n5th\n6th\n7th\n8th\n9th\na\na\'\na\'s\na/c\na1\naa\naaa\naah\naahed\naahing\naahs\naal\naalii\naaliis\naals\naam\naardvark\naardvarks\naardwolf\naardwolves\naargh\naaron\naaronic\naarrgh\naarrghh\naas\naasvogel\naasvogels\nab\naba\nabac\nabaca\nabacas\nabacate\nabacaxi\nabacay\nabaci\nabacinate\nabacination\nabacisci\nabaciscus\nabacist\naback\nabacli\nabacot\nabacterial\nabactinal\nabactinally\nabaction\nabactor\nabaculi\nabaculus\nabacus\nabacuses\nabada\nabaddon\nabadejo\nabadengo\nabadia\nabaff\nabaft\nabaisance\nabaised\nabaiser\nabaisse\nabaissed\nabaka\nabakas\nabalation\nabalienate\nabalienated\nabalienating\nabalienation\nabalone\nabalones\nabamp\nabampere\nabamperes\nabamps\nab

In [52]:
#dict_new = dicti.split("\\n")
dict_new = dicti.split("\n")
dict_new[49] #the first 49 parts are not words so we have to remove them from the list

'a1'

In [53]:
dict_final = []
df = 0
for i in range (50,len(dict_new)):
    forfinal = dict_new[i]
    forfinal = forfinal.replace("'","")
    dict_final.insert(df,forfinal)
    df =df +1
dict_final[0] #This is the original dictionary with which we will check each word

'aa'

In [55]:
#And now we will find each html file which words has inside
empty = []
wordsin = []
ocin = []
for num in range(len(list500_names)):
    line = str(list500_sites[num]) 
    wordcount={}
    corwordcount={}
    simeiastiksis = ["/",".",",","=",">","<","?","|",":","_","]","[","$","&","%","(",")","{","}",'"',";","\\","-","!","+","#","=","@","^","*","'"]
    for ss in range(len(simeiastiksis)):
        simeio = simeiastiksis[ss]     
        line = line.replace(simeio, " ")
    for word1 in line.split():
        word1 = word1.lower()
        if word1 in dict_final:
            if word1 not in wordcount:
                wordcount[word1] = 1
            else:
                wordcount[word1] += 1     
    wordsin_local = []
    wl = 0
    ocin_local = []
    for k,v in wordcount.items():
           #print (k,v)
           wordsin_local.insert(wl,str(k))
           ocin_local.insert(wl,str(v))
           wl = wl +1
    wordsin.insert(num,wordsin_local) # final list with all the words in each site
    ocin.insert(num,ocin_local)  #final list with all the occurencies of the words in each site
    print('finished site: ', str(num + 1))

('finished site: ', '1')
('finished site: ', '2')
('finished site: ', '3')
('finished site: ', '4')
('finished site: ', '5')
('finished site: ', '6')
('finished site: ', '7')
('finished site: ', '8')
('finished site: ', '9')
('finished site: ', '10')
('finished site: ', '11')
('finished site: ', '12')
('finished site: ', '13')
('finished site: ', '14')
('finished site: ', '15')
('finished site: ', '16')
('finished site: ', '17')
('finished site: ', '18')
('finished site: ', '19')
('finished site: ', '20')
('finished site: ', '21')
('finished site: ', '22')
('finished site: ', '23')
('finished site: ', '24')


In [56]:
#Create the dataframe for the words and unique words
d8 = {'company' : pd.Series(list500_names, index=[nm]),'url' : pd.Series(list500_url, index=[nm])}
wordss = pd.DataFrame(d8)    
wordss 

company                             url
0                    Walmart                 www.walmart.com
1                Exxon Mobil              www.exxonmobil.com
2                      Apple                   www.apple.com
3         Berkshire Hathaway       www.berkshirehathaway.com
4                   McKesson                www.mckesson.com
5         UnitedHealth Group       www.unitedhealthgroup.com
6                 CVS Health               www.cvshealth.com
7             General Motors                      www.gm.com
8                 Ford Motor                    www.ford.com
9                   AT&amp;T                     www.att.com
10          General Electric                      www.ge.com
11         AmerisourceBergen       www.amerisourcebergen.com
12                   Verizon                 www.verizon.com
13                   Chevron                 www.chevron.com
14                    Costco                  www.costco.com
15                    Kroger             www.thekrogerco.com
16                Amazon.com                  www.amazon.com
17  Walgreens Boots Alliance  www.walgreensbootsalliance.com
18                        HP                      www.hp.com
19           Cardinal Health                www.cardinal.com
20   Express Scripts Holding         www.express-scripts.com
21         J.P. Morgan Chase           www.jpmorganchase.com
22                    Boeing                  www.boeing.com
23                 Microsoft               www.microsoft.com

In [57]:
#Create the two lists we will need in order to make the dataframe
l1 = []
l2 = []
for num in range(len(list500_names)):   
    line = str(list500_sites[num]) 
    total_words = len(wordsin[num])
    occurencies = ocin[num] 
    l1.insert(num,total_words)
    count = 0 
    for a in occurencies :
        if a == '1':
            count = count + 1
    l2.insert(num,count)
wordss['total words'] = pd.Series(l1, index=sizess.index)
wordss['unique words'] = pd.Series(l2, index=sizess.index)          
wordss                 

company                             url  total words  \
0                    Walmart                 www.walmart.com         1509   
1                Exxon Mobil              www.exxonmobil.com          799   
2                      Apple                   www.apple.com          393   
3         Berkshire Hathaway       www.berkshirehathaway.com          170   
4                   McKesson                www.mckesson.com          512   
5         UnitedHealth Group       www.unitedhealthgroup.com          827   
6                 CVS Health               www.cvshealth.com          700   
7             General Motors                      www.gm.com          435   
8                 Ford Motor                    www.ford.com         1217   
9                   AT&amp;T                     www.att.com          913   
10          General Electric                      www.ge.com          468   
11         AmerisourceBergen       www.amerisourcebergen.com            6   
12                   Verizon                 www.verizon.com          293   
13                   Chevron                 www.chevron.com          555   
14                    Costco                  www.costco.com         1559   
15                    Kroger             www.thekrogerco.com          515   
16                Amazon.com                  www.amazon.com         1494   
17  Walgreens Boots Alliance  www.walgreensbootsalliance.com          476   
18                        HP                      www.hp.com          419   
19           Cardinal Health                www.cardinal.com          712   
20   Express Scripts Holding         www.express-scripts.com          311   
21         J.P. Morgan Chase           www.jpmorganchase.com          776   
22                    Boeing                  www.boeing.com          538   
23                 Microsoft               www.microsoft.com          397   

    unique words  
0            432  
1            150  
2            126  
3            103  
4            180  
5            318  
6            255  
7            111  
8            505  
9            223  
10           142  
11             5  
12           127  
13           145  
14           564  
15           282  
16           503  
17           125  
18           156  
19           275  
20           143  
21           257  
22           160  
23           135